# Text extraction on image
Inga Ulusoy, SSC, July 2022

In [1]:
# if running on google colab
# flake8-noqa-cell
import os

if "google.colab" in str(get_ipython()):
    # update python version
    # install setuptools
    !pip install setuptools==61 -qqq
    # install misinformation
    !pip install git+https://github.com/ssciwr/misinformation.git -qqq
    # mount google drive for data and API key
    from google.colab import drive

    drive.mount("/content/drive")

In [2]:
import misinformation
from misinformation import utils as mutils
from misinformation import display as mdisplay

In [3]:
# download the models if they are not there yet
!python -m spacy download en_core_web_md
!python -m textblob.download_corpora

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/42.8 MB ? eta -:--:--

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.1/42.8 MB 1.6 MB/s eta 0:00:27

     ╸━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.9/42.8 MB 13.0 MB/s eta 0:00:04

     ━━━━━━━━╺━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.6/42.8 MB 60.7 MB/s eta 0:00:01

     ━━━━━━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.6/42.8 MB 109.1 MB/s eta 0:00:01

...

[nltk_data] Downloading package conll2000 to /home/runner/nltk_data...


[nltk_data]   Unzipping corpora/conll2000.zip.


[nltk_data] Downloading package movie_reviews to
[nltk_data]     /home/runner/nltk_data...


[nltk_data]   Unzipping corpora/movie_reviews.zip.


Finished.


In [4]:
images = mutils.find_files(path="data", limit=10)

In [5]:
mydict = mutils.initialize_dict(images)

## google cloud vision API
First 1000 images per month are free.

## Inspect the elements per image

In [6]:
mdisplay.explore_analysis(mydict, identify="text-on-image")

## Or directly analyze for further processing

In [7]:
for key in mydict:
    mydict[key] = misinformation.text.TextDetector(
        mydict[key], analyse_text=True
    ).analyse_image()

## Convert to dataframe and write csv

In [8]:
outdict = mutils.append_data_to_dict(mydict)
df = mutils.dump_df(outdict)

In [9]:
# check the dataframe
df.head(10)

filename                                               text  \
0    data/102730_eng.png  400 DEATHS GET E-BOOK X AN Corporation ncy Ser...   
1  data/102141_2_eng.png  CORONAVIRUS QUARANTINE CORONAVIRUS OUTBREAK BE...   
2   data/106349S_por.png  NEWS URGENTE SAMSUNG AO VIVO Rio de Janeiro NO...   

  text_language                                       text_english  \
0            en  400 DEATHS GET E-BOOK X AN Corporation ncy Ser...   
1            en  CORONAVIRUS QUARANTINE CORONAVIRUS OUTBREAK BE...   
2            pt  NEWS URGENT SAMSUNG LIVE Rio de Janeiro NEW CO...   

                                          text_clean  \
0  DEATHS GET E - BOOK X AN Corporation Services ...   
1  CORONAVIRUS QUARANTINE CORONAVIRUS OUTBREAK BE...   
2  NEWS URGENT SAMSUNG LIVE Rio de Janeiro NEW CO...   

                                text_english_correct  polarity  subjectivity  
0  400 DEATHS GET E-BOOK X of Corporation ney Ser... -0.125000      0.375000  
1  CORONAVIRUS QUARANTINE CORONAVIRUS OUTBREAK BE...  0.000000      0.000000  
2  NEWS URGENT SAMSUNG LIVE Rio de Janeiro NEW CO... -0.106818      0.588636

In [10]:
# Write the csv
df.to_csv("./data_out.csv")